In [3]:
import datetime as dt
from pathlib import Path
import xarray as xr
import glob

In [7]:
locs = {
    'uk': {'lon': slice(-12, 3) , 'lat': slice(60, 49), 'reason': 'student'},  
}

vars = ['tp', 't2m', 'pet', 'spei']
varnames = [['tp'], ['t2m'], ['pet_thornthwaite'], ['spei_pearson_03', 'spei_pearson_06', 'spei_pearson_12', 'spei_pearson_24']]

In [9]:
def t():
    return dt.datetime.now().strftime("%H:%M:%S")

def td(start):
    return (dt.datetime.now() - start).total_seconds()

t_start = dt.datetime.now()

print(f"{t()} START script")

# prepare point lists once
locnames = list(locs.keys())
lats  = [locs[n]["lat"] for n in locnames]
lons  = [locs[n]["lon"] for n in locnames]

for locname, lon, lat in zip(locnames, lons, lats):

    out_ds = None

    for var, varn_ in zip(vars, varnames):
    
        with xr.open_dataset(f'../ERA5_LowRes/ERA5_LowRes_Monthly_{var}.nc', chunks={'time': -1}) as ds:
    
            for varn in varn_:
    
                # Point selection
                out = ds.sel(
                    latitude=lat,
                    longitude=lon,
                ).load()

                if out_ds is None:
                    out_ds = out[['time', 'latitude', 'longitude']]
                
                out_ds[varn] = (('time', 'latitude', 'longitude'), out[varn].data)
                out_ds[varn].attrs = out[varn].attrs

                if varn == 'tp':
                    out_ds[varn].attrs['units'] = 'm/day'

                if ('pet' in varn) or ('spei' in varn):
                    out_ds[varn].attrs['units'] = 'mm/month'
        
    odir = f"timeseries/{locname}"
    Path(odir).mkdir(parents=True, exist_ok=True)
    
    outpath = (
        f"{odir}/era5_{locname}_monthly.nc"
    )
    out_ds.to_netcdf(outpath)

10:52:58 START script


In [18]:
print('Done')

Done


In [21]:
import xarray as xr
import glob
from pathlib import Path

vars = ['pr', 'tas', 'pet', 'spei']
varnames = [['pr'], ['tas'], ['pet_thornthwaite'],
            ['spei_pearson_03', 'spei_pearson_06',
             'spei_pearson_12', 'spei_pearson_24']]
scenarios = ['ssp126', 'ssp245', 'ssp370', 'ssp585']


for locname, lon, lat in zip(locnames, lons, lats):

    print(locname)

    for ssp in scenarios:

        # store outputs as: out[var][gcm] = DataArray(time)
        collected = {v: {} for group in varnames for v in group}

        gcms = set()

        print(ssp)

        for var, varn_list in zip(vars, varnames):

            print(var)

            files = glob.glob(f'../CMIP6/075deg/*/*_{ssp}_regridded_{var}.nc')

            for f in files:

                gcm = f.split('075deg/')[1].split('/')[0]
                gcms.add(gcm)

                with xr.open_dataset(f) as ds:
                    pt = ds.sel(latitude=lat, longitude=lon).load()

                    for varn in varn_list:
                        arr = pt[varn]
                        collected[varn][gcm] = arr

        # concatenate across GCMs → (time, lat, lon, gcm)
        gcm_list = sorted(gcms)
    
        data_vars = {}
        for varn, d in collected.items():
            da = xr.concat([d[gcm] for gcm in gcm_list],
                           dim="gcm", coords="minimal")
            da = da.assign_coords(gcm=gcm_list)
    
            if ('pet' in varn) or ('spei' in varn):
                da.attrs['units'] = 'mm/month'
    
            data_vars[varn] = da
    
        out_ds = xr.Dataset(data_vars)
        
        # Output path
        odir = f"timeseries/{locname}"
        Path(odir).mkdir(parents=True, exist_ok=True)
        outpath = f"{odir}/gcm_{ssp}_{locname}_monthly.nc"

        out_ds.to_netcdf(outpath)

uk
ssp126
pr
tas
pet
spei
ssp245
pr
tas
pet
spei
ssp370
pr
tas
pet
spei
ssp585
pr
tas
pet
spei


In [24]:
'done'

'done'